# Analyse des relevés météorologiques de Marignane

## Importation du fichier, choix des colonnes et changement des noms

Le fichier regroupe des observations réalisées entre le 1 janvier 2010 et début décembre 2018 (date à laquelle le fichier a été téléchargé). Les colonnes précipitations sont divisées en plusieurs sections :

- Précipitations dans la dernière heure
- Précipitations dans les 3 dernières heures
- Précipitations dans les 6 dernières heures
- Précipitations dans les 12 dernières heures
- Précipitations dans les 24 dernières heures


Les observations concernant les 24h sont d'abord faites une fois par jour à 7h ou 8h. Mais à partir de décembre 2014 celles-ci changent et se les précipitations des dernières 24h sont calculées à chaque relevé.


In [2]:
import pandas as pd
import numpy as np
import datetime as dt

# Chemin du fichier.
path = "./data/meteo_marignane.csv" 


# On créé un DataFrame (df) à partir de ce csv, en précisant le séparateur (';'), et en précisant qu'on ne veut que des strings.
df = pd.read_csv(path, sep = ";", dtype=str)

# On importe seulement les colonnes désirées.
df = df[['Date','Précipitations dans la dernière heure', 'Précipitations dans les 3 dernières heures', \
         'Précipitations dans les 6 dernières heures', 'Précipitations dans les 12 dernières heures', \
         'Précipitations dans les 24 dernières heures']].copy() 

# On les renomme avec des noms plus courts.
df.rename(columns={'Précipitations dans la dernière heure': 'LastHour',\
                   'Précipitations dans les 3 dernières heures':'Last3Hours',\
                   'Précipitations dans les 6 dernières heures':'Last6Hours',\
                   'Précipitations dans les 12 dernières heures':'Last12Hours',\
                   'Précipitations dans les 24 dernières heures':'Last24Hours'}, inplace = True) 

## Nettoyage des données

In [3]:
# On divise la string en une liste comportant deux éléments, ce qu'il y a avant le '+'(la date et l'heure) et après (le GMT+).
df['Date'] = df['Date'].str.split('+', n= 1, expand = False)

#On créé une nouvelle colonne qui comporte la première moitié de la liste créée précédemment, donc la date et l'heure.
df['DateTime'] = df['Date'].str[0]

# On enlève le 'T', on le remplace par un espace et on convertit le tout en format datetime.
df['DateTime'] = pd.to_datetime(df['DateTime'].str.replace('T', ' '))

# On copie le deuxième élément de la liste dans une nouvelle colonne nommée 'GMT+'.
df['GMT+'] = df['Date'].str[1]

# On efface l'ancienne colonne 'Date'.
df.drop(columns=['Date'], inplace = True)

# On peut éventuellement placer la date en index, mais finalement j'ai trouvé ça moins pratique.
#df.set_index('DateTime', inplace = True)
# Dans ce cas là on le reclasse pour qu'il soit classé par ordre chronologique.
#df.sort_index() 

df = df.sort_values(by = 'DateTime') # On reclasse le df
df = df.reset_index(drop = True) # On créé un nouvel index basé sur l'ordre chronologique.

# Dommage que cette ligne ne fonctionne pas, ça aurait été plus classe, du coup j'ai fait autrement.
#pd.to_numeric(df['LastHour','Last3Hours','Last6Hours','Last12Hours','Last24Hours'], downcast='integer')

df['LastHour'] = pd.to_numeric(df['LastHour'], downcast='integer') # On convertit les string en variables numériques
df['Last3Hours'] = pd.to_numeric(df['Last3Hours'], downcast='integer')
df['Last6Hours'] = pd.to_numeric(df['Last6Hours'], downcast='integer')
df['Last12Hours'] = pd.to_numeric(df['Last12Hours'], downcast='integer')
df['Last24Hours'] = pd.to_numeric(df['Last24Hours'], downcast='integer')

## Informations générales sur le df

In [4]:
# Un coup d'oeil rapide
df.head(15)

LastHour  Last3Hours  Last6Hours  Last12Hours  Last24Hours  \
0        0.2         0.2         0.2          NaN          NaN   
1        0.0         0.2         NaN          NaN          NaN   
2        NaN         NaN         NaN          NaN          NaN   
3        1.0         3.0         NaN          NaN          NaN   
4        0.4         1.0         4.0          NaN          NaN   
5        0.0         0.2         NaN          NaN          NaN   
6        0.0         0.0         NaN          4.0          NaN   
7        0.0         0.0         NaN          NaN          NaN   
8        0.0         0.0         0.0          NaN          NaN   
9        0.0         0.0         NaN          NaN          NaN   
10       0.0         0.0         NaN          0.0          3.8   
11       0.0         0.0         NaN          NaN          NaN   
12       0.0         0.0         0.0          NaN          NaN   
13       0.0         0.0         NaN          NaN          NaN   
14       0.0         0.0         NaN          0.0          NaN   

              DateTime   GMT+  
0  2010-01-01 01:00:00  01:00  
1  2010-01-01 04:00:00  01:00  
2  2010-01-01 07:00:00  01:00  
3  2010-01-01 10:00:00  01:00  
4  2010-01-01 13:00:00  01:00  
5  2010-01-01 16:00:00  01:00  
6  2010-01-01 19:00:00  01:00  
7  2010-01-01 22:00:00  01:00  
8  2010-01-02 01:00:00  01:00  
9  2010-01-02 04:00:00  01:00  
10 2010-01-02 07:00:00  01:00  
11 2010-01-02 10:00:00  01:00  
12 2010-01-02 13:00:00  01:00  
13 2010-01-02 16:00:00  01:00  
14 2010-01-02 19:00:00  01:00

In [5]:
# Date du premier relevé
df['DateTime'].min()

Timestamp('2010-01-01 01:00:00')

In [6]:
# Date du dernier relevé (début décembre puisque j'ai téléchargé les données à ce moment là)
df['DateTime'].max()

Timestamp('2018-12-03 22:00:00')

In [7]:
# À quelles heures les relevés ont-ils lieu ?
df['DateTime'].dt.hour.unique()

array([ 1,  4,  7, 10, 13, 16, 19, 22,  5,  8, 11, 14, 17, 20, 23,  2],
      dtype=int64)

In [8]:
# Le nombre de dates différentes dans le df :
len(df['DateTime'].dt.date.unique())

3216

In [9]:
# Commande pour afficher uniquement la date d'une entrée (dans le bon format)
df['DateTime'][1212].strftime('%Y-%m-%d')

'2010-06-01'

In [10]:
# Afficher tous les relevés d'une date précise
for i in df.index:
    if df['DateTime'][i].strftime('%Y-%m-%d') == '2010-12-18':
        print (df.iloc[i,:])

LastHour                         0
Last3Hours                       0
Last6Hours                       0
Last12Hours                    NaN
Last24Hours                    NaN
DateTime       2010-12-18 01:00:00
GMT+                         01:00
Name: 2808, dtype: object
LastHour                         0
Last3Hours                     NaN
Last6Hours                     NaN
Last12Hours                    NaN
Last24Hours                    NaN
DateTime       2010-12-18 04:00:00
GMT+                         01:00
Name: 2809, dtype: object
LastHour                         0
Last3Hours                       0
Last6Hours                     NaN
Last12Hours                    NaN
Last24Hours                    NaN
DateTime       2010-12-18 07:00:00
GMT+                         01:00
Name: 2810, dtype: object
LastHour                         0
Last3Hours                       0
Last6Hours                     NaN
Last12Hours                    NaN
Last24Hours                    NaN
DateTime    

## Affichage de la pluviométrie

Ici par exemple, on affiche les relevés où il a plu plus de 55mm durant les dernières 24h.

In [11]:
for i in df.index:
    if df['Last24Hours'][i] > 55:
        print(df['DateTime'][i], df['Last24Hours'][i])

2011-11-06 07:00:00 56.6
2012-05-21 08:00:00 63.3
2012-10-27 08:00:00 55.4
2018-01-26 19:00:00 57.7
2018-01-26 22:00:00 66.2
2018-01-27 01:00:00 66.4
2018-01-27 04:00:00 66.4
2018-01-27 07:00:00 66.6
2018-01-27 10:00:00 64.2
2018-01-27 13:00:00 64.2
2018-10-10 23:00:00 64.5
2018-10-11 02:00:00 71.8
2018-10-11 05:00:00 71.8
2018-10-11 08:00:00 71.8
2018-10-11 11:00:00 67.6


### Création d'un nouveau DF, et export en CSV

On crée un nouveau dataframe qui associe à chaque date le revelé effectué durant les dernières 24h (donc ceux effectués à 7h ou à 8h).
Apparemment, il est conseillé de passer par un dictionnaire pour recréer un nouveau data frame (gain de performances).

In [12]:
dict_temp= {} # Dictionnaire vide
for i in df.index:
    if (df['DateTime'][i].hour == 7 or df['DateTime'][i].hour == 8): # Uniquement les relevés effectués à 7h ou à 8h
        dict_temp[df['DateTime'][i].strftime('%Y-%m-%d')] = (df['Last24Hours'][i]) # On créé une nouvelle entrée que l'on associe avec la valeur

# On passe par les items puisque dans notre dictionnaire nous n'avons qu'une date (clé) associé à un nombre (valeur), et pas à une liste contenue dans la valeur.
df_24h = pd.DataFrame(list(dict_temp.items()), columns = ['Date', 'Pluie (mm)']) 

In [13]:
df_24h.head(5)

Date  Pluie (mm)
0  2010-01-01         NaN
1  2010-01-02         3.8
2  2010-01-03         0.0
3  2010-01-04         1.4
4  2010-01-05         0.2

Nombre de lignes du nouveau df :

In [14]:
len(df_24h)

3212

Nombre de lignes où la valeur est manquante :

In [15]:
df_24h.isna().sum()

Date           0
Pluie (mm)    52
dtype: int64

Pour afficher les lignes nulles :

In [16]:
df_24h[df_24h.isnull().any(axis=1)]

Date  Pluie (mm)
0     2010-01-01         NaN
37    2010-02-07         NaN
75    2010-03-17         NaN
187   2010-07-07         NaN
347   2010-12-14         NaN
351   2010-12-18         NaN
357   2010-12-24         NaN
372   2011-01-08         NaN
482   2011-04-28         NaN
533   2011-06-18         NaN
557   2011-07-12         NaN
558   2011-07-13         NaN
560   2011-07-15         NaN
703   2011-12-05         NaN
746   2012-01-17         NaN
811   2012-03-22         NaN
944   2012-08-02         NaN
1077  2012-12-13         NaN
1090  2012-12-26         NaN
1407  2013-11-08         NaN
1585  2014-05-05         NaN
1935  2015-04-21         NaN
1957  2015-05-13         NaN
1998  2015-06-23         NaN
2129  2015-11-26         NaN
2170  2016-01-06         NaN
2179  2016-01-15         NaN
2185  2016-01-21         NaN
2190  2016-01-26         NaN
2198  2016-02-03         NaN
2310  2016-05-25         NaN
2323  2016-06-07         NaN
2360  2016-07-14         NaN
2466  2016-10-28         NaN
2561  2017-01-31         NaN
2563  2017-02-02         NaN
2621  2017-04-01         NaN
2647  2017-04-27         NaN
2648  2017-04-28         NaN
2653  2017-05-03         NaN
2750  2017-08-08         NaN
2769  2017-08-27         NaN
2770  2017-08-28         NaN
2843  2017-11-09         NaN
2898  2018-01-05         NaN
2925  2018-02-01         NaN
2941  2018-02-17         NaN
3031  2018-05-18         NaN
3086  2018-07-20         NaN
3115  2018-08-21         NaN
3181  2018-11-02         NaN
3201  2018-11-22         NaN

En examinant les journées où les données sont manquantes, on voit qu'elles correspondent à des jours sans pluie. On peut donc les remplacer par 0.

In [17]:
df_24h = df_24h.fillna(0)

#### Export du nouveau CSV

In [18]:
df_24h.to_csv('releves_journalier_marignane.csv', index=False)

### Analyse des données

### Autres manipulations utiles

Afficher les heures des revelés pour une date précise (il y a peut-être une manière plus simple).

In [18]:
for i in df.index:
    if df['DateTime'][i].strftime('%Y-%m-%d') == '2018-05-18':
        print (df['DateTime'][i])

2018-05-18 02:00:00
2018-05-18 05:00:00
2018-05-18 08:00:00
2018-05-18 11:00:00
2018-05-18 14:00:00
2018-05-18 17:00:00
2018-05-18 20:00:00
2018-05-18 23:00:00


Afficher toutes les entrées pour une date précise.

In [19]:
for i in df.index:
    if df['DateTime'][i].strftime('%Y-%m-%d') == '2018-05-18':
        print (df.iloc[i,:])

LastHour                         0
Last3Hours                       0
Last6Hours                       0
Last12Hours                    NaN
Last24Hours                    NaN
DateTime       2018-05-18 02:00:00
GMT+                         02:00
Name: 24250, dtype: object
LastHour                         0
Last3Hours                       0
Last6Hours                       0
Last12Hours                      0
Last24Hours                    NaN
DateTime       2018-05-18 05:00:00
GMT+                         02:00
Name: 24251, dtype: object
LastHour                         0
Last3Hours                       0
Last6Hours                       0
Last12Hours                      0
Last24Hours                    NaN
DateTime       2018-05-18 08:00:00
GMT+                         02:00
Name: 24252, dtype: object
LastHour                         0
Last3Hours                       0
Last6Hours                       0
Last12Hours                      0
Last24Hours                    NaN
DateTime 